In [3]:
# basic libraries
import pandas as pd
import numpy as np
import numpy.random as rd
import gc
import multiprocessing as mp
import os
import sys
import pickle
from glob import glob
import math
from datetime import datetime as dt
from pathlib import Path
import scipy.stats as st
import re
import shutil
from tqdm import tqdm_notebook as tqdm
import datetime
ts_conv = np.vectorize(datetime.datetime.fromtimestamp) # 秒ut(10桁) ⇒ 日付

# グラフ描画系
import matplotlib
from matplotlib import font_manager
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from matplotlib import rc

from matplotlib import animation as ani
from IPython.display import Image

plt.rcParams["patch.force_edgecolor"] = True
#rc('text', usetex=True)
from IPython.display import display # Allows the use of display() for DataFrames
import seaborn as sns
sns.set(style="whitegrid", palette="muted", color_codes=True)
sns.set_style("whitegrid", {'grid.linestyle': '--'})
red = sns.xkcd_rgb["light red"]
green = sns.xkcd_rgb["medium green"]
blue = sns.xkcd_rgb["denim blue"]

# pandas formatting
pd.set_option("display.max_colwidth", 100)
pd.set_option("display.max_rows", None)
pd.set_option("display.max_columns", None)
pd.options.display.float_format = '{:,.5f}'.format

%matplotlib inline
%config InlineBackend.figure_format='retina'

In [4]:
# ngboost
from ngboost.ngboost import NGBoost
from ngboost.learners import default_tree_learner
from ngboost.scores import MLE
from ngboost.distns import Normal, LogNormal

# skleran
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

## Data preparation

In [5]:
X, y = load_boston(True)
rd.seed(71)
X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2)

In [7]:
%%time
rd.seed(71)
ngb = NGBoost(Base=default_tree_learner, Dist=Normal,
              Score=MLE(), natural_gradient=True, verbose=True,)
ngb.fit(X_train, y_train, X_val=X_valid, Y_val=y_valid)

xx = np.linspace(0, 60, 200)
y_preds = ngb.predict(X_valid)
y_preds_dist = ngb.pred_dist_pdf(X_valid, y_range=xx)

[iter 0] loss=3.6583 val_loss=3.5465 scale=0.5000 norm=3.4222
[iter 100] loss=3.1249 val_loss=3.1240 scale=1.0000 norm=3.9650
[iter 200] loss=2.7303 val_loss=2.8042 scale=1.0000 norm=2.5054
[iter 300] loss=2.4069 val_loss=2.6114 scale=1.0000 norm=1.9669
== Quitting at iteration / VAL 374 (val_loss=2.5606)
CPU times: user 1.77 s, sys: 8.28 ms, total: 1.77 s
Wall time: 1.77 s


In [8]:
plt.figure(figsize=(25, 120))
for idx in tqdm(np.arange(X_valid.shape[0])):
    
    plt.subplot(35, 3, idx+1)
    plt.plot(xx, y_preds_dist[idx])
    
    plt.vlines(y_preds[idx], 0, max(y_preds_dist[idx]), "r", label="ngb pred")
    plt.vlines(y_valid[idx], 0, max(y_preds_dist[idx]), "pink", label="ground truth")
    plt.legend(loc="best")
    plt.title(f"idx: {idx}")
    plt.xlim(xx[0], xx[-1])
plt.tight_layout()
plt.show()